# Business Problem
- Using the bike sharing dataset to predict number of bikes rentals per hour

#Data Preprocessing


In [0]:
display(dbutils.fs.ls('/databricks-datasets'))

path name size modificationTime dbfs:/databricks-datasets/COVID/ COVID/ 0 1727904900716 dbfs:/databricks-datasets/README.md README.md 976 1532502332000 dbfs:/databricks-datasets/Rdatasets/ Rdatasets/ 0 1727904900716 dbfs:/databricks-datasets/SPARK_README.md SPARK_README.md 3359 1455505270000 dbfs:/databricks-datasets/adult/ adult/ 0 1727904900716 dbfs:/databricks-datasets/airlines/ airlines/ 0 1727904900716 dbfs:/databricks-datasets/amazon/ amazon/ 0 1727904900716 dbfs:/databricks-datasets/asa/ asa/ 0 1727904900716 dbfs:/databricks-datasets/atlas_higgs/ atlas_higgs/ 0 1727904900716 dbfs:/databricks-datasets/bikeSharing/ bikeSharing/ 0 1727904900716 dbfs:/databricks-datasets/cctvVideos/ cctvVideos/ 0 1727904900716 dbfs:/databricks-datasets/credit-card-fraud/ credit-card-fraud/ 0 1727904900716 dbfs:/databricks-datasets/cs100/ cs100/ 0 1727904900716 dbfs:/databricks-datasets/cs110x/ cs110x/ 0 1727904900716 dbfs:/databricks-datasets/cs190/ cs190/ 0 1727904900716 dbfs:/databricks-datasets/data.gov/ data.gov/ 0 1727904900716 dbfs:/databricks-datasets/definitive-guide/ definitive-guide/ 0 1727904900716 dbfs:/databricks-datasets/delta-sharing/ delta-sharing/ 0 1727904900716 dbfs:/databricks-datasets/flights/ flights/ 0 1727904900716 dbfs:/databricks-datasets/flower_photos/ flower_photos/ 0 1727904900716 dbfs:/databricks-datasets/flowers/ flowers/ 0 1727904900716 dbfs:/databricks-datasets/genomics/ genomics/ 0 1727904900716 dbfs:/databricks-datasets/hail/ hail/ 0 1727904900716 dbfs:/databricks-datasets/identifying-campaign-effectiveness/ identifying-campaign-effectiveness/ 0 1727904900716 dbfs:/databricks-datasets/iot/ iot/ 0 1727904900716 dbfs:/databricks-datasets/iot-stream/ iot-stream/ 0 1727904900716 dbfs:/databricks-datasets/learning-spark/ learning-spark/ 0 1727904900716 dbfs:/databricks-datasets/learning-spark-v2/ learning-spark-v2/ 0 1727904900716 dbfs:/databricks-datasets/lending-club-loan-stats/ lending-club-loan-stats/ 0 1727904900716 dbfs:/databricks-datasets/med-images/ med-images/ 0 1727904900716 dbfs:/databricks-datasets/media/ media/ 0 1727904900716 dbfs:/databricks-datasets/mnist-digits/ mnist-digits/ 0 1727904900716 dbfs:/databricks-datasets/news20.binary/ news20.binary/ 0 1727904900716 dbfs:/databricks-datasets/nyctaxi/ nyctaxi/ 0 1727904900716 dbfs:/databricks-datasets/nyctaxi-with-zipcodes/ nyctaxi-with-zipcodes/ 0 1727904900716 dbfs:/databricks-datasets/online_retail/ online_retail/ 0 1727904900716 dbfs:/databricks-datasets/overlap-join/ overlap-join/ 0 1727904900716 dbfs:/databricks-datasets/power-plant/ power-plant/ 0 1727904900716 dbfs:/databricks-datasets/retail-org/ retail-org/ 0 1727904900716 dbfs:/databricks-datasets/rwe/ rwe/ 0 1727904900717 dbfs:/databricks-datasets/sai-summit-2019-sf/ sai-summit-2019-sf/ 0 1727904900717 dbfs:/databricks-datasets/sample_logs/ sample_logs/ 0 1727904900717 dbfs:/databricks-datasets/samples/ samples/ 0 1727904900717 dbfs:/databricks-datasets/sfo_customer_survey/ sfo_customer_survey/ 0 1727904900717 dbfs:/databricks-datasets/sms_spam_collection/ sms_spam_collection/ 0 1727904900717 dbfs:/databricks-datasets/songs/ songs/ 0 1727904900717 dbfs:/databricks-datasets/structured-streaming/ structured-streaming/ 0 1727904900717 dbfs:/databricks-datasets/timeseries/ timeseries/ 0 1727904900717 dbfs:/databricks-datasets/tpch/ tpch/ 0 1727904900717 dbfs:/databricks-datasets/travel_recommendations_realtime/ travel_recommendations_realtime/ 0 1727904900717 dbfs:/databricks-datasets/warmup/ warmup/ 0 1727904900717 dbfs:/databricks-datasets/weather/ weather/ 0 1727904900717 dbfs:/databricks-datasets/wiki/ wiki/ 0 1727904900717 dbfs:/databricks-datasets/wikipedia-datasets/ wikipedia-datasets/ 0 1727904900717 dbfs:/databricks-datasets/wine-quality/ wine-quality/ 0 1727904900717

In [0]:
df = spark.read.csv('/databricks-datasets/bikeSharing/data-001/hour.csv', header=True, inferSchema=True)
df.cache()

DataFrame[instant: int, dteday: date, season: int, yr: int, mnth: int, hr: int, holiday: int, weekday: int, workingday: int, weathersit: int, temp: double, atemp: double, hum: double, windspeed: double, casual: int, registered: int, cnt: int]

In [0]:
df.head()

Row(instant=1, dteday=datetime.date(2011, 1, 1), season=1, yr=0, mnth=1, hr=0, holiday=0, weekday=6, workingday=0, weathersit=1, temp=0.24, atemp=0.2879, hum=0.81, windspeed=0.0, casual=3, registered=13, cnt=16)

In [0]:
df.count()

17379

In [0]:
df = df.drop("instant").drop("dteday").drop("casual").drop("registered")

In [0]:
df.printSchema()

root
 |-- season: integer (nullable = true)
 |-- yr: integer (nullable = true)
 |-- mnth: integer (nullable = true)
 |-- hr: integer (nullable = true)
 |-- holiday: integer (nullable = true)
 |-- weekday: integer (nullable = true)
 |-- workingday: integer (nullable = true)
 |-- weathersit: integer (nullable = true)
 |-- temp: double (nullable = true)
 |-- atemp: double (nullable = true)
 |-- hum: double (nullable = true)
 |-- windspeed: double (nullable = true)
 |-- cnt: integer (nullable = true)



In [0]:
# splitting the data into training and test sets 
# We split the data on 4 seasons. Keeping intact 
# the order of seasons. 
from pyspark.sql.functions import col
from pyspark.sql import DataFrame

def split_seasons(df: DataFrame):
    seasons = [1, 2, 3, 4]
    train_dfs = []
    test_dfs = []
    
    for season in seasons:
        season_df = df.filter(col("season") == season)
        train, test = season_df.randomSplit([0.8, 0.2], seed=42)
        train_dfs.append(train)
        test_dfs.append(test)
    
    train_df = train_dfs[0].union(train_dfs[1]).union(train_dfs[2]).union(train_dfs[3])
    test_df = test_dfs[0].union(test_dfs[1]).union(test_dfs[2]).union(test_dfs[3])
    
    return train_df, test_df

train_df, test_df = split_seasons(df)
display(train_df)
display(test_df)

season yr mnth hr holiday weekday workingday weathersit temp atemp hum windspeed cnt 1 0 1 0 0 0 0 1 0.04 0.0758 0.57 0.1045 22 1 0 1 0 0 0 0 1 0.1 0.0758 0.42 0.3881 25 1 0 1 0 0 0 0 1 0.26 0.303 0.56 0.0 39 1 0 1 0 0 0 0 2 0.46 0.4545 0.88 0.2985 17 1 0 1 0 0 1 1 1 0.06 0.0606 0.41 0.194 7 1 0 1 0 0 1 1 1 0.22 0.197 0.44 0.3582 5 1 0 1 0 0 2 1 1 0.14 0.1667 0.59 0.1045 12 1 0 1 0 0 2 1 1 0.16 0.1818 0.55 0.1045 5 1 0 1 0 0 2 1 2 0.16 0.1364 0.69 0.2836 9 1 0 1 0 0 3 1 1 0.2 0.2576 0.64 0.0 6 1 0 1 0 0 3 1 2 0.22 0.2273 0.69 0.1343 17 1 0 1 0 0 3 1 2 0.22 0.2727 0.93 0.0 3 1 0 1 0 0 4 1 1 0.14 0.1212 0.59 0.2836 7 1 0 1 0 0 4 1 1 0.18 0.2424 0.55 0.0 11 1 0 1 0 0 4 1 1 0.26 0.2273 0.56 0.3881 13 1 0 1 0 0 5 1 2 0.2 0.197 0.64 0.194 17 1 0 1 0 0 5 1 2 0.2 0.2121 0.75 0.1343 9 1 0 1 0 0 5 1 2 0.24 0.2273 0.7 0.2537 21 1 0 1 0 0 6 0 1 0.18 0.2424 0.55 0.0 28 1 0 1 0 0 6 0 1 0.22 0.197 0.64 0.3582 28 1 0 1 0 0 6 0 1 0.24 0.2879 0.81 0.0 16 1 0 1 0 0 6 0 2 0.18 0.197 0.51 0.1642 25 1 0 1 0 1 1 0 2 0.2 0.197 0.47 0.2239 17 1 0 1 1 0 0 0 1 0.1 0.0606 0.42 0.4627 12 1 0 1 1 0 0 0 1 0.14 0.2121 0.8 0.0 29 1 0 1 1 0 0 0 1 0.26 0.2727 0.56 0.1343 23 1 0 1 1 0 0 0 2 0.44 0.4394 0.94 0.2537 17 1 0 1 1 0 1 1 1 0.04 0.0455 0.45 0.194 1 1 0 1 1 0 1 1 1 0.2 0.1667 0.44 0.4179 2 1 0 1 1 0 1 1 1 0.22 0.2121 0.64 0.2537 7 1 0 1 1 0 2 1 1 0.14 0.1515 0.59 0.1642 3 1 0 1 1 0 2 1 1 0.16 0.1818 0.59 0.1045 2 1 0 1 1 0 2 1 2 0.16 0.1667 0.69 0.1642 5 1 0 1 1 0 3 1 1 0.16 0.197 0.74 0.0896 6 1 0 1 1 0 3 1 2 0.16 0.1818 0.86 0.1045 6 1 0 1 1 0 3 1 2 0.24 0.2424 0.65 0.1343 5 1 0 1 1 0 3 1 3 0.22 0.2273 0.93 0.1343 7 1 0 1 1 0 5 1 1 0.1 0.1212 0.54 0.1642 5 1 0 1 1 0 5 1 2 0.2 0.2121 0.75 0.1343 3 1 0 1 1 0 6 0 1 0.22 0.2273 0.64 0.194 20 1 0 1 1 0 6 0 1 0.22 0.2727 0.8 0.0 40 1 0 1 1 0 6 0 2 0.04 0.0 0.41 0.3881 12 1 0 1 1 0 6 0 2 0.18 0.2121 0.55 0.0896 16 1 0 1 1 1 1 0 2 0.2 0.197 0.44 0.194 16 1 0 1 2 0 0 0 1 0.02 0.0606 0.62 0.1343 18 1 0 1 2 0 0 0 1 0.1 0.0606 0.46 0.4627 11 1 0 1 2 0 0 0 1 0.16 0.2273 0.8 0.0 11 1 0 1 2 0 0 0 1 0.26 0.2879 0.56 0.0896 16 1 0 1 2 0 1 1 1 0.12 0.1212 0.5 0.2239 3 1 0 1 2 0 1 1 1 0.22 0.2273 0.64 0.194 1 1 0 1 2 0 2 1 1 0.14 0.1515 0.63 0.1343 1 1 0 1 2 0 2 1 1 0.16 0.1515 0.69 0.2239 2 1 0 1 2 0 2 1 2 0.16 0.1515 0.55 0.194 3 1 0 1 2 0 3 1 1 0.14 0.1515 0.86 0.1343 1 1 0 1 2 0 3 1 3 0.22 0.2273 0.69 0.194 10 1 0 1 2 0 3 1 3 0.22 0.2273 0.93 0.1343 3 1 0 1 2 0 4 1 1 0.14 0.1212 0.5 0.3582 2 1 0 1 2 0 4 1 1 0.16 0.2273 0.64 0.0 2 1 0 1 2 0 4 1 1 0.26 0.2727 0.56 0.0 2 1 0 1 2 0 5 1 1 0.1 0.1212 0.54 0.1343 1 1 0 1 2 0 5 1 2 0.2 0.197 0.69 0.2239 1 1 0 1 2 0 5 1 3 0.24 0.2424 0.75 0.1642 2 1 0 1 2 0 6 0 1 0.22 0.2273 0.64 0.1642 15 1 0 1 2 0 6 0 1 0.22 0.2727 0.8 0.0 32 1 0 1 2 0 6 0 2 0.04 0.0303 0.41 0.2537 11 1 0 1 2 0 6 0 2 0.16 0.197 0.59 0.0896 12 1 0 1 2 0 6 0 2 0.18 0.2424 0.55 0.0 16 1 0 1 2 1 1 0 2 0.18 0.1667 0.43 0.2537 8 1 0 1 3 0 0 0 1 0.02 0.0606 0.62 0.1343 5 1 0 1 3 0 0 0 1 0.1 0.0758 0.46 0.4179 4 1 0 1 3 0 0 0 1 0.14 0.2121 0.93 0.0 8 1 0 1 3 0 0 0 1 0.22 0.2727 0.69 0.0 15 1 0 1 3 0 0 0 2 0.46 0.4545 0.94 0.194 6 1 0 1 3 0 1 1 1 0.04 0.0303 0.45 0.2537 1 1 0 1 3 0 1 1 1 0.12 0.1212 0.5 0.2239 1 1 0 1 3 0 1 1 1 0.22 0.2273 0.64 0.194 2 1 0 1 3 0 4 1 1 0.14 0.1212 0.5 0.3284 3 1 0 1 3 0 4 1 1 0.26 0.2576 0.56 0.1642 1 1 0 1 3 0 5 1 1 0.1 0.1364 0.54 0.1045 1 1 0 1 3 0 5 1 2 0.2 0.2273 0.75 0.1045 1 1 0 1 3 0 5 1 3 0.22 0.2121 0.8 0.2985 1 1 0 1 3 0 6 0 1 0.2 0.2121 0.64 0.1343 8 1 0 1 3 0 6 0 1 0.24 0.2879 0.75 0.0 13 1 0 1 3 0 6 0 2 0.16 0.2273 0.59 0.0 8 1 0 1 3 0 6 0 3 0.18 0.197 0.55 0.1642 7 1 0 1 3 1 1 0 2 0.18 0.1818 0.43 0.194 2 1 0 1 4 0 0 0 1 0.08 0.0909 0.53 0.194 1 1 0 1 4 0 0 0 1 0.14 0.2121 0.93 0.0 1 1 0 1 4 0 0 0 1 0.26 0.2576 0.56 0.1642 1 1 0 1 4 0 0 0 2 0.46 0.4545 0.94 0.194 3 1 0 1 4 0 1 1 1 0.02 0.0606 0.48 0.1343 1 1 0 1 4 0 1 1 1 0.1 0.1212 0.54 0.1343 3 1 0 1 4 0 1 1 1 0.16 0.1364 0.47 0.3881 1 1 0 1 4 0 1 1 1 0.2 0.197 0.59 0.2239 2 1 0 1 4 0 2 1 1 0.14 0.1818 0.63 0.0896 2 

season yr mnth hr holiday weekday workingday weathersit temp atemp hum windspeed cnt 1 0 1 0 0 0 0 1 0.16 0.1818 0.8 0.1045 33 1 0 1 0 0 1 1 1 0.12 0.1212 0.5 0.2836 5 1 0 1 0 0 1 1 2 0.24 0.2273 0.65 0.2239 7 1 0 1 0 0 3 1 2 0.16 0.197 0.86 0.0896 7 1 0 1 0 0 5 1 1 0.12 0.1364 0.5 0.194 14 1 0 1 0 0 6 0 1 0.04 0.0303 0.45 0.2537 13 1 0 1 1 0 0 0 1 0.04 0.0758 0.57 0.1045 13 1 0 1 1 0 1 1 1 0.12 0.1212 0.5 0.2836 1 1 0 1 1 0 4 1 1 0.14 0.1212 0.5 0.2836 2 1 0 1 1 0 4 1 1 0.16 0.2273 0.64 0.0 4 1 0 1 1 0 4 1 1 0.26 0.2727 0.56 0.0 5 1 0 1 1 0 5 1 2 0.2 0.197 0.69 0.2239 7 1 0 1 1 0 5 1 2 0.24 0.2273 0.7 0.2537 6 1 0 1 1 0 6 0 2 0.16 0.197 0.59 0.0896 20 1 0 1 2 0 0 0 2 0.42 0.4242 1.0 0.2836 9 1 0 1 2 0 3 1 1 0.16 0.197 0.74 0.0896 2 1 0 1 2 0 5 1 2 0.2 0.2121 0.75 0.1642 2 1 0 1 3 0 6 0 2 0.04 0.0303 0.41 0.2836 7 1 0 1 4 0 2 1 1 0.14 0.1667 0.74 0.1045 1 1 0 1 4 0 4 1 1 0.14 0.1212 0.5 0.2537 4 1 0 1 4 0 4 1 1 0.26 0.2576 0.56 0.1642 1 1 0 1 4 0 4 1 2 0.16 0.197 0.64 0.0896 1 1 0 1 5 0 0 0 2 0.04 0.0758 0.57 0.1045 3 1 0 1 5 0 1 1 1 0.02 0.0606 0.48 0.1343 5 1 0 1 5 1 1 0 2 0.18 0.197 0.43 0.1642 1 1 0 1 6 0 1 1 1 0.16 0.1364 0.69 0.3284 37 1 0 1 6 0 3 1 1 0.12 0.1515 0.93 0.1343 16 1 0 1 6 0 4 1 1 0.12 0.1515 0.54 0.1343 28 1 0 1 6 0 5 1 1 0.1 0.1818 0.54 0.0 17 1 0 1 7 0 0 0 1 0.14 0.2121 0.86 0.0 3 1 0 1 7 0 1 1 2 0.16 0.1364 0.64 0.2836 72 1 0 1 7 0 6 0 1 0.02 0.0152 0.44 0.2836 8 1 0 1 8 0 0 0 1 0.1 0.0909 0.49 0.2836 10 1 0 1 8 0 2 1 1 0.14 0.1515 0.69 0.1642 179 1 0 1 8 0 3 1 2 0.24 0.2576 0.93 0.1045 197 1 0 1 9 0 0 0 1 0.12 0.0758 0.46 0.5224 19 1 0 1 9 0 3 1 3 0.22 0.2121 0.87 0.2985 58 1 0 1 9 0 5 1 1 0.14 0.1515 0.69 0.1343 117 1 0 1 9 0 5 1 3 0.18 0.2121 0.86 0.0896 101 1 0 1 9 0 6 0 1 0.16 0.1818 0.64 0.1343 33 1 0 1 9 0 6 0 3 0.16 0.1818 0.93 0.1045 20 1 0 1 10 0 0 0 1 0.14 0.1061 0.43 0.3881 49 1 0 1 10 0 5 1 1 0.2 0.1667 0.47 0.4627 63 1 0 1 10 0 6 0 1 0.18 0.197 0.59 0.1642 59 1 0 1 10 0 6 0 1 0.38 0.3939 0.76 0.2537 36 1 0 1 10 1 1 0 2 0.16 0.1515 0.5 0.2537 57 1 0 1 11 0 0 0 1 0.16 0.1212 0.4 0.5224 49 1 0 1 11 0 3 1 1 0.26 0.2273 0.33 0.3284 46 1 0 1 11 0 3 1 3 0.22 0.197 0.93 0.3284 41 1 0 1 11 0 6 0 2 0.18 0.197 0.64 0.1343 64 1 0 1 12 0 2 1 1 0.22 0.2273 0.51 0.1642 78 1 0 1 12 0 2 1 2 0.2 0.2273 0.51 0.1045 57 1 0 1 12 0 3 1 2 0.3 0.3182 0.81 0.0896 70 1 0 1 12 0 5 1 2 0.2 0.197 0.37 0.2537 59 1 0 1 13 0 2 1 2 0.26 0.2727 0.56 0.1343 93 1 0 1 13 0 5 1 1 0.2 0.1515 0.21 0.5821 73 1 0 1 13 0 6 0 1 0.28 0.2576 0.38 0.2985 101 1 0 1 14 0 2 1 2 0.2 0.2273 0.59 0.0896 63 1 0 1 14 0 5 1 3 0.22 0.2727 0.8 0.0 38 1 0 1 15 0 0 0 1 0.16 0.1364 0.28 0.3582 77 1 0 1 15 0 2 1 2 0.16 0.197 0.8 0.0896 47 1 0 1 15 0 2 1 2 0.22 0.2273 0.87 0.1642 35 1 0 1 15 0 4 1 2 0.32 0.3182 0.45 0.194 70 1 0 1 15 0 6 0 2 0.32 0.3182 0.36 0.194 129 1 0 1 16 0 0 0 1 0.2 0.1667 0.34 0.4478 92 1 0 1 16 0 0 0 3 0.34 0.3333 0.71 0.1642 76 1 0 1 16 0 4 1 1 0.22 0.2273 0.55 0.194 24 1 0 1 16 0 6 0 1 0.12 0.1364 0.28 0.194 83 1 0 1 16 0 6 0 1 0.24 0.2424 0.6 0.1642 107 1 0 1 16 1 1 0 2 0.2 0.2121 0.47 0.1642 82 1 0 1 17 0 0 0 1 0.22 0.2121 0.37 0.2537 105 1 0 1 17 0 1 1 1 0.24 0.2273 0.3 0.2239 157 1 0 1 17 0 2 1 2 0.22 0.2273 0.82 0.194 125 1 0 1 17 0 4 1 1 0.22 0.2424 0.55 0.1045 84 1 0 1 17 0 6 0 1 0.16 0.1212 0.37 0.5522 69 1 0 1 17 0 6 0 1 0.24 0.2879 0.6 0.0 91 1 0 1 17 0 6 0 2 0.44 0.4394 0.82 0.2836 67 1 0 1 18 0 0 0 1 0.26 0.2576 0.65 0.1642 65 1 0 1 18 0 0 0 2 0.36 0.3333 0.46 0.3284 53 1 0 1 18 0 1 1 1 0.2 0.197 0.4 0.2239 155 1 0 1 18 0 2 1 1 0.26 0.2576 0.48 0.194 182 1 0 1 18 0 2 1 2 0.22 0.2273 0.8 0.1642 133 1 0 1 18 0 6 0 3 0.42 0.4242 0.88 0.2537 35 1 0 1 19 0 2 1 2 0.22 0.2273 0.8 0.1343 99 1 0 1 19 0 4 1 1 0.16 0.1515 0.47 0.2537 99 1 0 1 19 0 4 1 1 0.26 0.2273 0.56 0.3284 152 1 0 1 20 0 0 0 1 0.3 0.2727 0.39 0.3582 22 1 0 1 20 0 1 1 3 0.16 0.1667 0.59 0.1642 78 1 0 1 20 0 2 1 3 0.16 0.1515 0.93 0.194 32 1 0 1 20 0 3 1 1 0.16 0.1364 0.5 0.3284 56 1 0 1 20 0 3 1 1 0.32 0.303 0.49 0.2985 76 1 0 1 20 0 5 1 1 0.1 0.0758 0.33

In [0]:
train_df.select("season").distinct().display()
test_df.select("season").distinct().display()

season 1 2 3 4

season 1 2 3 4

In [0]:
display(train_df.select("hr","cnt"))

hr cnt 0 22 0 25 0 39 0 17 0 7 0 5 0 12 0 5 0 9 0 6 0 17 0 3 0 7 0 11 0 13 0 17 0 9 0 21 0 28 0 28 0 16 0 25 0 17 1 12 1 29 1 23 1 17 1 1 1 2 1 7 1 3 1 2 1 5 1 6 1 6 1 5 1 7 1 5 1 3 1 20 1 40 1 12 1 16 1 16 2 18 2 11 2 11 2 16 2 3 2 1 2 1 2 2 2 3 2 1 2 10 2 3 2 2 2 2 2 2 2 1 2 1 2 2 2 15 2 32 2 11 2 12 2 16 2 8 3 5 3 4 3 8 3 15 3 6 3 1 3 1 3 2 3 3 3 1 3 1 3 1 3 1 3 8 3 13 3 8 3 7 3 2 4 1 4 1 4 1 4 3 4 1 4 3 4 1 4 2 4 2 4 2 4 2 4 1 4 1 4 3 4 1 4 3 4 5 4 1 4 3 5 1 5 3 5 2 5 3 5 3 5 8 5 4 5 9 5 6 5 5 5 3 5 7 5 1 5 3 5 6 5 4 5 8 5 5 5 4 5 5 5 1 5 5 5 1 6 1 6 1 6 1 6 2 6 15 6 31 6 30 6 36 6 36 6 27 6 33 6 32 6 8 6 35 6 36 6 27 6 16 6 34 6 3 6 2 6 2 6 2 6 2 6 5 7 6 7 2 7 3 7 1 7 84 7 77 7 64 7 94 7 108 7 99 7 54 7 88 7 90 7 30 7 72 7 101 7 95 7 70 7 68 7 84 7 60 7 10 7 5 7 3 7 9 7 13 8 19 8 18 8 12 8 8 8 177 8 154 8 188 8 185 8 238 8 217 8 128 8 195 8 72 8 202 8 219 8 249 8 158 8 217 8 210 8 157 8 27 8 23 8 34 8 8 8 15 8 33 9 28 9 32 9 38 9 20 9 102 9 88 9 94 9 112 9 100 9 130 9 144 9 81 9 115 9 109 9 139 9 122 9 143 9 134 9 166 9 40 9 34 9 14 9 47 10 58 10 79 10 64 10 53 10 40 10 44 10 31 10 69 10 42 10 54 10 55 10 39 10 57 10 47 10 28 10 45 10 57 10 38 10 44 10 63 10 49 10 53 10 61 10 55 11 99 11 59 11 93 11 70 11 46 11 51 11 30 11 48 11 57 11 35 11 61 11 35 11 52 11 59 11 37 11 68 11 53 11 59 11 67 11 30 11 72 11 56 11 63 11 62 11 64 12 116 12 83 12 104 12 97 12 93 12 61 12 63 12 68 12 52 12 3 12 106 12 55 12 79 12 48 12 52 12 84 12 84 12 61 12 78 12 29 12 89 12 84 12 70 12 98 12 78 12 80 13 87 13 75 13 118 13 84 13 75 13 61 13 60 13 54 13 54 13 97 13 22 13 52 13 49 13 71 13 78 13 47 13 83 13 67 13 98 13 77 13 73 13 31 13 84 13 102 13 65 13 94 13 93 14 110 14 72 14 91 14 122 14 59 14 77 14 45 14 86 14 47 14 63 14 28 14 68 14 44 14 62 14 75 14 36 14 42 14 70 14 81 14 62 14 64 14 50 14 75 14 95 14 118 14 99 14 106 14 86 15 82 15 113 15 109 15 74 15 57 15 72 15 44 15 45 15 65 15 84 15 49 15 62 15 82 15 43 15 60 15 62 15 65 15 68 15 72 15 41 15 103 15 74 15 120 15 110 15 93 16 65 16 99 16 123 16 70 16 74 16 76 16 86 16 83 16 76 16 61 16 116 16 68 16 89 16 104 16 36 16 78 16 86 16 91 16 97 16 90 16 80 16 87 16 76 16 128 16 93 17 55 17 62 17 77 17 65 17 184 17 178 17 161 17 212 17 222 17 136 17 139 17 190 17 197 17 26 17 162 17 172 17 215 17 161 17 159 17 149 17 187 17 67 17 83 17 71 18 49 18 48 18 67 18 153 18 157 18 156 18 225 18 95 18 137 18 169 18 161 18 144 18 104 18 163 18 185 18 120 18 123 18 139 18 109 18 54 18 55 18 68 18 84 18 92 19 50 19 41 19 61 19 55 19 30 19 106 19 95 19 110 19 111 19 112 19 146 19 51 19 83 19 132 19 112 19 79 19 112 19 96 19 95 19 92 19 89 19 59 19 30 19 58 19 74 19 37 19 60 20 35 20 38 20 57 20 33 20 81 20 74 20 52 20 119 20 54 20 83 20 89 20 64 20 59 20 69 20 126 20 51 20 62 20 28 20 43 20 41 20 33 21 25 21 20 21 28 21 31 21 38 21 59 21 52 21 56 21 48 21 45 21 41 21 20 21 57 21 59 21 40 21 38 21 57 21 41 21 52 21 39 21 58 21 39 21 37 21 36 21 57 21 34 22 28 22 9 22 21 22 24 22 35 22 34 22 53 22 35 22 33 22 29 22 42 22 59 22 30 22 52 22 56 22 26 22 36 22 36 22 34 22 32 22 26 22 28 22 13 23 21 23 8 23 18 23 21 23 18 23 12 23 24 23 17 23 11 23 40 23 20 23 19 23 15 23 16 23 23 23 31 23 27 23 23 23 15 23 27 23 33 23 22 23 33 23 44 23 39 23 4 0 39 0 17 0 34 0 39 0 15 0 11 0 30 0 10 0 17 0 6 0 15 0 2 0 12 0 11 0 17 0 16 0 32 0 13 0 9 0 28 0 29 0 39 1 24 1 44 1 37 1 5 1 7 1 5 1 3 1 4 1 7 1 4 1 9 1 5 1 7 1 6 1 7 1 7 1 8 1 7 1 10 1 24 1 27 1 31 1 13 2 17 2 20 2 20 2 2 2 3 2 2 2 2 2 1 2 4 2 2 2 4 2 6 2 3 2 3 2 7 2 3 2 15 2 12 2 17 2 17 2 4 3 18 3 13 3 11 3 12 3 1 3 2 3 2 3 1 3 2 3 2 3 1 3 1 3 2 3 4 3 8 3 1 3 2 3 10 3 8 3 7 3 5 4 2 4 2 4 2 4 2 4 1 4 1 4 1 4 4 4 1 4 4 4 3 4 2 4 8 4 1 5 1 5 10 5 5 5 4 5 2 5 3 5 7 5 8 5 5 5 3 5 2 5 4 5 12 5 6 5 7 5 6 5 7 5 1 5 3 5 10 5 9 5 3 6 3 6 5 6 30 6 26 6 30 6 39 6 43 6 36 6 33 6 18 6 39 6 47 6 26 6 24 6 28 6 50 6 11 6 2 6 7 6 6 6 4 6 8 7 2 7 8 7 14 7 3 7 92 7 105 7 100 7 40 7 52 7 99 7 96 7 108 7 49 7 99 7 104 7 126 7 87 7 35 7 11 7 22 7 22 8 24 8 23 8 35 8 12 8 256 8 230 8 22

Databricks visualization. Run in Databricks to view.

In [0]:
display(test_df.select("hr","cnt"))

hr cnt 0 33 0 5 0 7 0 7 0 14 0 13 1 13 1 1 1 2 1 4 1 5 1 7 1 6 1 20 2 9 2 2 2 2 3 7 4 1 4 4 4 1 4 1 5 3 5 5 5 1 6 37 6 16 6 28 6 17 7 3 7 72 7 8 8 10 8 179 8 197 9 19 9 58 9 117 9 101 9 33 9 20 10 49 10 63 10 59 10 36 10 57 11 49 11 46 11 41 11 64 12 78 12 57 12 70 12 59 13 93 13 73 13 101 14 63 14 38 15 77 15 47 15 35 15 70 15 129 16 92 16 76 16 24 16 83 16 107 16 82 17 105 17 157 17 125 17 84 17 69 17 91 17 67 18 65 18 53 18 155 18 182 18 133 18 35 19 99 19 99 19 152 20 22 20 78 20 32 20 56 20 76 20 53 20 68 20 45 20 36 21 28 21 43 21 48 21 27 22 15 22 21 22 20 22 33 22 27 22 34 22 30 23 6 23 19 23 20 23 28 0 19 0 8 0 14 0 30 0 37 1 16 1 8 1 3 1 18 2 22 2 3 2 3 2 1 3 1 3 1 3 11 4 1 4 2 4 3 4 1 5 3 5 4 6 2 6 1 6 28 6 7 6 22 6 58 7 95 7 98 7 87 7 74 7 116 7 4 7 19 8 255 8 199 8 155 9 55 9 135 9 116 9 133 9 140 10 89 10 51 10 49 10 81 11 112 11 53 11 64 11 113 11 47 11 90 12 152 12 126 12 36 12 55 12 55 12 71 12 119 12 52 13 182 13 50 13 75 13 62 13 155 14 161 14 90 14 79 14 81 14 69 14 91 14 85 14 55 15 64 15 90 15 171 16 157 16 147 16 103 16 122 16 80 16 71 16 71 16 56 17 146 17 121 17 187 17 216 17 196 17 190 17 255 17 177 17 211 17 327 18 209 18 170 18 147 19 128 19 118 20 89 20 63 20 71 20 29 21 27 21 56 21 54 21 66 21 91 21 83 21 72 21 54 22 69 22 45 22 41 22 46 23 39 23 39 23 77 23 31 0 52 0 9 0 23 0 6 1 12 1 8 1 18 2 30 2 3 2 2 3 3 3 2 3 4 3 1 4 3 5 3 5 1 5 10 5 11 5 8 6 28 6 46 6 35 6 4 7 37 8 37 8 257 8 282 8 45 9 44 10 84 10 68 10 117 10 103 11 60 11 73 11 89 12 194 12 86 12 167 13 221 13 105 13 97 13 125 13 80 13 12 13 157 14 39 14 77 14 72 14 119 14 12 14 95 14 174 15 85 15 205 16 256 16 71 16 304 17 233 17 202 17 313 18 156 18 225 18 201 18 82 19 152 20 88 20 70 20 38 20 76 20 70 21 75 21 55 21 72 22 53 22 63 23 19 23 18 23 23 23 27 23 50 0 12 0 10 0 27 1 4 1 6 1 16 2 2 2 7 2 26 3 6 3 18 4 10 4 3 5 8 5 9 5 4 6 1 6 10 7 229 7 92 8 5 8 217 8 205 8 49 8 18 9 56 10 43 10 60 10 118 11 111 11 145 11 91 12 170 12 273 13 20 13 131 13 121 14 86 14 153 15 91 15 253 16 167 16 101 16 195 17 115 17 356 18 280 18 207 20 56 22 33 22 17 23 16 23 31 0 96 0 91 0 15 0 14 0 9 0 17 0 42 1 9 1 21 1 12 1 50 1 12 2 2 2 4 2 6 2 7 2 26 3 32 3 7 3 8 3 17 3 20 3 13 4 6 4 2 4 3 4 3 4 4 5 23 5 26 5 6 6 80 6 59 6 7 7 17 7 240 7 126 7 256 7 239 7 20 7 33 8 493 8 354 8 220 8 64 8 53 9 198 9 211 9 255 9 68 9 230 9 263 10 149 10 60 10 116 10 108 10 90 10 103 10 45 10 109 11 255 11 99 11 62 11 88 11 153 11 139 11 75 11 46 11 99 11 114 11 296 11 179 12 234 12 194 12 161 12 144 12 154 12 124 13 65 13 118 13 220 13 373 13 445 14 188 14 267 14 73 14 117 14 362 14 512 15 330 15 155 15 222 15 156 15 226 16 205 16 155 16 219 16 118 16 224 16 294 16 174 17 460 17 281 17 495 17 385 17 332 17 422 17 349 17 322 18 106 18 385 18 423 18 98 18 383 18 406 18 143 18 126 19 110 19 112 19 89 19 220 19 156 19 281 19 265 19 330 19 206 19 102 19 85 20 95 20 111 20 132 20 136 20 103 20 90 21 69 21 162 21 120 21 185 21 174 22 58 22 114 22 142 22 59 22 39 23 52 23 37 23 56 23 101 23 38 23 85 0 10 0 31 0 38 0 43 1 14 1 12 1 22 1 18 1 18 2 27 2 3 2 4 2 7 2 7 2 9 2 20 3 1 3 5 3 8 4 9 4 2 4 7 5 16 5 22 5 32 5 19 5 16 5 2 6 5 6 72 6 72 6 100 6 67 6 91 6 71 6 82 6 5 6 9 7 226 7 272 7 28 8 62 8 559 8 520 8 90 8 120 9 87 9 93 9 262 9 228 9 275 9 270 9 244 9 138 10 71 10 85 10 44 10 224 11 182 11 103 11 71 11 153 11 163 11 270 12 255 12 118 12 138 12 158 12 216 12 281 13 190 13 184 13 137 14 135 14 134 14 124 14 146 14 216 14 263 15 272 15 195 15 54 15 174 15 216 15 221 15 232 16 231 16 75 16 229 16 343 16 143 17 530 17 523 17 487 17 539 17 610 17 465 17 396 18 96 18 181 18 468 18 300 18 242 19 69 19 263 19 291 19 306 19 311 19 335 19 267 19 172 20 88 20 214 20 219 20 212 20 204 20 97 20 171 20 105 20 77 21 147 21 188 21 190 21 233 21 177 21 134 21 48 22 55 22 101 23 36 23 56 23 91 23 70 23 74 0 26 0 11 0 54 1 15 1 15 1 21 1 20 1 26 1 44 2 4 2 42 3 3 3 4 3 21 4 14 4 1 4 3 4 5 4 3 4 4 5 26 5 10 6 100 6 121 6 109 7 23 7 268 7 334 7 262 7 86 8 66 8 516 8 662 9 118 9 281 9 331 9 351 9 

Databricks visualization. Run in Databricks to view.

#Train the ML pipeline

### A few steps to be done
- VectorAssembler to assemble features into a feature vector
- VectorIndexer Identifies the column that should be treated as categorical
- GBTRegressor
- Cross Validator


In [0]:
from pyspark.ml.feature import VectorAssembler,VectorIndexer

featureCols = df.columns
featureCols.remove("cnt")

vectorAssembler = VectorAssembler(inputCols=featureCols,outputCol="rawFeatures")
vectorIndexer = VectorIndexer(inputCol="rawFeatures",outputCol="features",maxCategories=4)

In [0]:
from pyspark.ml.regression import GBTRegressor

gbt = GBTRegressor(labelCol="cnt", maxIter=2)

In [0]:
from pyspark.ml.tuning import CrossValidator,ParamGridBuilder
from pyspark.ml.evaluation import RegressionEvaluator

paramGrid = ParamGridBuilder() \
  .addGrid(gbt.maxDepth, [5,7, 10])\
  .addGrid(gbt.maxIter, [2, 5])\
  .build()

evaluator = RegressionEvaluator(metricName="rmse",labelCol=gbt.getLabelCol(),predictionCol=gbt.getPredictionCol())  
cv = CrossValidator(estimator=gbt, estimatorParamMaps=paramGrid, evaluator=evaluator, numFolds=2)   
      
      

In [0]:
from pyspark.ml import Pipeline 
pipeline = Pipeline(stages=[vectorAssembler,vectorIndexer,cv])

In [0]:
pipelineModel = pipeline.fit(train_df)

#Make predictions and evaluate


In [0]:
predictions  = pipelineModel.transform(test_df)

In [0]:
display(predictions.select("cnt","prediction",*featureCols))

cnt prediction season yr mnth hr holiday weekday workingday weathersit temp atemp hum windspeed 33 22.26313143175853 1 0 1 0 0 0 0 1 0.16 0.1818 0.8 0.1045 5 10.221963814637018 1 0 1 0 0 1 1 1 0.12 0.1212 0.5 0.2836 7 15.988471530723679 1 0 1 0 0 1 1 2 0.24 0.2273 0.65 0.2239 7 10.572782207872647 1 0 1 0 0 3 1 2 0.16 0.197 0.86 0.0896 14 12.997364884155735 1 0 1 0 0 5 1 1 0.12 0.1364 0.5 0.194 13 21.899005680577883 1 0 1 0 0 6 0 1 0.04 0.0303 0.45 0.2537 13 25.69101999147162 1 0 1 1 0 0 0 1 0.04 0.0758 0.57 0.1045 1 4.041135927926781 1 0 1 1 0 1 1 1 0.12 0.1212 0.5 0.2836 2 4.041135927926781 1 0 1 1 0 4 1 1 0.14 0.1212 0.5 0.2836 4 5.615989388220726 1 0 1 1 0 4 1 1 0.16 0.2273 0.64 0.0 5 5.318153694396007 1 0 1 1 0 4 1 1 0.26 0.2727 0.56 0.0 7 3.776159746701501 1 0 1 1 0 5 1 2 0.2 0.197 0.69 0.2239 6 5.869082490080596 1 0 1 1 0 5 1 2 0.24 0.2273 0.7 0.2537 20 23.959715496751407 1 0 1 1 0 6 0 2 0.16 0.197 0.59 0.0896 9 36.13800780674331 1 0 1 2 0 0 0 2 0.42 0.4242 1.0 0.2836 2 3.1735931506920645 1 0 1 2 0 3 1 1 0.16 0.197 0.74 0.0896 2 6.323297793839548 1 0 1 2 0 5 1 2 0.2 0.2121 0.75 0.1642 7 9.563644039490791 1 0 1 3 0 6 0 2 0.04 0.0303 0.41 0.2836 1 1.768284946984864 1 0 1 4 0 2 1 1 0.14 0.1667 0.74 0.1045 4 1.5353678647816678 1 0 1 4 0 4 1 1 0.14 0.1212 0.5 0.2537 1 1.8189340986173583 1 0 1 4 0 4 1 1 0.26 0.2576 0.56 0.1642 1 2.6946894098897913 1 0 1 4 0 4 1 2 0.16 0.197 0.64 0.0896 3 -1.2996525601148183 1 0 1 5 0 0 0 2 0.04 0.0758 0.57 0.1045 5 5.432313882342304 1 0 1 5 0 1 1 1 0.02 0.0606 0.48 0.1343 1 0.669150927570907 1 0 1 5 1 1 0 2 0.18 0.197 0.43 0.1642 37 29.650063658783544 1 0 1 6 0 1 1 1 0.16 0.1364 0.69 0.3284 16 30.23016801386821 1 0 1 6 0 3 1 1 0.12 0.1515 0.93 0.1343 28 30.23016801386821 1 0 1 6 0 4 1 1 0.12 0.1515 0.54 0.1343 17 29.123931669935647 1 0 1 6 0 5 1 1 0.1 0.1818 0.54 0.0 3 6.151949377820884 1 0 1 7 0 0 0 1 0.14 0.2121 0.86 0.0 72 70.50980533081392 1 0 1 7 0 1 1 2 0.16 0.1364 0.64 0.2836 8 9.044674736959475 1 0 1 7 0 6 0 1 0.02 0.0152 0.44 0.2836 10 25.923334151728223 1 0 1 8 0 0 0 1 0.1 0.0909 0.49 0.2836 179 202.11328475983368 1 0 1 8 0 2 1 1 0.14 0.1515 0.69 0.1642 197 204.03047150076546 1 0 1 8 0 3 1 2 0.24 0.2576 0.93 0.1045 19 32.049490515093844 1 0 1 9 0 0 0 1 0.12 0.0758 0.46 0.5224 58 123.47118487137415 1 0 1 9 0 3 1 3 0.22 0.2121 0.87 0.2985 117 124.1140246784426 1 0 1 9 0 5 1 1 0.14 0.1515 0.69 0.1343 101 113.55105906975373 1 0 1 9 0 5 1 3 0.18 0.2121 0.86 0.0896 33 56.44353618046698 1 0 1 9 0 6 0 1 0.16 0.1818 0.64 0.1343 20 30.903118666621225 1 0 1 9 0 6 0 3 0.16 0.1818 0.93 0.1045 49 81.80469348255126 1 0 1 10 0 0 0 1 0.14 0.1061 0.43 0.3881 63 48.647487180180654 1 0 1 10 0 5 1 1 0.2 0.1667 0.47 0.4627 59 93.12106916466418 1 0 1 10 0 6 0 1 0.18 0.197 0.59 0.1642 36 64.49111120226215 1 0 1 10 0 6 0 1 0.38 0.3939 0.76 0.2537 57 90.48046095818938 1 0 1 10 1 1 0 2 0.16 0.1515 0.5 0.2537 49 99.47928529160549 1 0 1 11 0 0 0 1 0.16 0.1212 0.4 0.5224 46 50.20232127947944 1 0 1 11 0 3 1 1 0.26 0.2273 0.33 0.3284 41 49.71638713168052 1 0 1 11 0 3 1 3 0.22 0.197 0.93 0.3284 64 91.16555309798383 1 0 1 11 0 6 0 2 0.18 0.197 0.64 0.1343 78 60.56127404001421 1 0 1 12 0 2 1 1 0.22 0.2273 0.51 0.1642 57 54.74499637940621 1 0 1 12 0 2 1 2 0.2 0.2273 0.51 0.1045 70 75.2481964780127 1 0 1 12 0 3 1 2 0.3 0.3182 0.81 0.0896 59 54.37453176544536 1 0 1 12 0 5 1 2 0.2 0.197 0.37 0.2537 93 59.40587742253068 1 0 1 13 0 2 1 2 0.26 0.2727 0.56 0.1343 73 61.90221985020121 1 0 1 13 0 5 1 1 0.2 0.1515 0.21 0.5821 101 108.8938804835752 1 0 1 13 0 6 0 1 0.28 0.2576 0.38 0.2985 63 53.677050760427285 1 0 1 14 0 2 1 2 0.2 0.2273 0.59 0.0896 38 43.972555596062406 1 0 1 14 0 5 1 3 0.22 0.2727 0.8 0.0 77 99.44118190052757 1 0 1 15 0 0 0 1 0.16 0.1364 0.28 0.3582 47 53.32463277960636 1 0 1 15 0 2 1 2 0.16 0.197 0.8 0.0896 35 56.981149512280176 1 0 1 15 0 2 1 2 0.22 0.2273 0.87 0.1642 70 82.88070795804221 1 0 1 15 0 4 1 2 0.32 0.3182 0.45 0.194 129 107.9535962946743 1 0 1 15 0 6 0 2 0.32 0.3182 0.36 0.194 92 96.92227645417104

In [0]:
rmse = evaluator.evaluate(predictions)
print(rmse)

55.981180299629955


In [0]:
import pyspark.sql.functions as F
predictions_with_residuals = predictions.withColumn("residual", F.col("cnt") - F.col("prediction"))
display(predictions_with_residuals.agg({'residual':'mean'}))

avg(residual) -1.9083890694392283